In [1]:
from itertools import product
import numpy as np
import random
import os
import shutil

In [2]:
# model_names = ['_'.join(list(_)) for _ in list(product(['TSGym'],
#                                                        ['False', 'True'], # gym_series_sampling
#                                                        ['None', 'Stat', 'RevIN', 'DishTS'], # gym_series_norm
#                                                        ['None', 'MA', 'MoEMA', 'DFT'], # gym_series_decomp
#                                                        ['False', 'True'], # gym_channel_independent
#                                                        ['inverted-encoding', 'series-encoding', 'series-patching'], # gym_input_embed
#                                                        ['Transformer'], # gym_network_architecture
#                                                        ['self-attention', 'auto-correlation', 'sparse-attention', 'frequency-enhanced-attention', 'destationary-attention'], # gym_attn
#                                                        ['True'], # gym_encoder_only
#                                                        ['HP'],
#                                                        ['48', '96', '192'], # sequence length
#                                                        ['64', '256', '512'], # d_model
#                                                        ['128', '512', '1024'], # d_ff
#                                                        ['2', '3'], # encoder layers
#                                                        ['10', '20', '50'], # training epochs
#                                                        ['0.0001', '0.001', '0.01'] # learning rate
#                                                        ))] +\
#                                                        ['_'.join(list(_)) for _ in list(product(['TSGym'],
#                                                        ['False', 'True'], # gym_series_sampling
#                                                        ['None', 'Stat', 'RevIN', 'DishTS'], # gym_series_norm
#                                                        ['None', 'MA', 'MoEMA', 'DFT'], # gym_series_decomp
#                                                        ['False', 'True'], # gym_channel_independent
#                                                        ['inverted-encoding', 'series-encoding', 'series-patching'], # gym_input_embed
#                                                        ['MLP', 'GRU'], # gym_network_architecture
#                                                        ['null'], # gym_attn
#                                                        ['True'], # gym_encoder_only
#                                                        ['HP'],
#                                                        ['48', '96', '192'], # sequence length
#                                                        ['64', '256', '512'], # d_model
#                                                        ['128', '512', '1024'], # d_ff
#                                                        ['2', '3'], # encoder layers
#                                                        ['10', '20', '50'], # training epochs
#                                                        ['0.0001', '0.001', '0.01'] # learning rate
#                                                        ))]


# model_names = ['_'.join(list(_)) for _ in list(product(['TSGym'],
#                                                        ['False', 'True'], # gym_series_sampling
#                                                        ['None', 'Stat', 'RevIN', 'DishTS'], # gym_series_norm
#                                                        ['None', 'MA', 'MoEMA', 'DFT'], # gym_series_decomp
#                                                        ['False', 'True'], # gym_channel_independent
#                                                        ['inverted-encoding', 'series-encoding', 'series-patching'], # gym_input_embed
#                                                        ['MLP', 'GRU'], # gym_network_architecture
#                                                        ['null'], # gym_attn
#                                                        ['True'], # gym_encoder_only
#                                                        ['HP'],
#                                                        ['48', '96', '192'], # sequence length
#                                                        ['64', '256', '512'], # d_model
#                                                        ['128', '512', '1024'], # d_ff
#                                                        ['2', '3'], # encoder layers
#                                                        ['10', '20', '50'], # training epochs
#                                                        ['0.0001', '0.001', '0.01'], # learning rate
#                                                        ))]

model_names = ['_'.join(list(_)) for _ in list(product(['TSGym'],
                                                       ['False', 'True'], # gym_series_sampling
                                                       ['None', 'Stat', 'RevIN', 'DishTS'], # gym_series_norm
                                                       ['None', 'MA', 'MoEMA', 'DFT'], # gym_series_decomp
                                                       ['False', 'True'], # gym_channel_independent
                                                       ['inverted-encoding', 'series-encoding', 'series-patching'], # gym_input_embed
                                                       ['MLP', 'GRU'], # gym_network_architecture
                                                       ['null'], # gym_attn
                                                       ['True'], # gym_encoder_only
                                                       ['HP'],
                                                       ['48', '96', '192'], # sequence length
                                                       ['64-256', '256-1024'], # d_model, d_ff
                                                       ['2', '3'], # encoder layers
                                                       ['10', '20'], # training epochs
                                                       ['0.0001', '0.001'], # learning rate
                                                       ['null', 'type1'] # learning rate strategy
                                                       ))]

In [3]:
random.seed(42)
print(len(model_names))
model_names = random.sample(model_names, 5000)

36864


In [4]:
for dataset in ['ECL', 'ETT', 'Exchange', 'ILI', 'Traffic', 'Weather']:
    # 模板文件路径
    template_path = f'/data/coding/chaochuan/TSGym/scripts/long_term_forecast/{dataset}_script/TSGym.sh'
    # 输出目录
    output_dir = f'/data/coding/chaochuan/TSGym/scripts/long_term_forecast/{dataset}_script/gym'

    # 确保输出目录存在
    if os.path.exists(output_dir):
        print('delete current folder!')
        shutil.rmtree(output_dir)
    os.makedirs(output_dir, exist_ok=True)

    # 读取模板内容
    with open(template_path, 'r') as file:
        template_content = file.read()

    # 对于每个模型名称，生成一个 shell 脚本
    for model_name in model_names:
        file_name = model_name

        HP = model_name[model_name.find('_HP')+4:]
        model_name = model_name[:model_name.find('_HP')]

        seq_len, dm_df, el, epochs, lr, lr_strategy = HP.split('_')
        dm, df = dm_df.split('-')[0], dm_df.split('-')[1]

        # 替换模型名称
        script_content = template_content.replace('$model_name', model_name)
        script_content = script_content.replace(f'$seq_len', seq_len)
        script_content = script_content.replace(f'$d_model', dm)
        script_content = script_content.replace(f'$d_ff', df)
        script_content = script_content.replace(f'$e_layers', el)
        script_content = script_content.replace(f'$train_epochs', epochs)
        script_content = script_content.replace(f'$learning_rate', lr)
        script_content = script_content.replace(f'$lradj', lr_strategy)
        
        # 定义输出文件名
        output_file = os.path.join(output_dir, f'{file_name}.sh')
        
        # 写入新的 shell 脚本
        with open(output_file, 'w') as file:
            file.write(script_content)

        print(f'Generated {output_file}')

delete current folder!
Generated /data/coding/chaochuan/TSGym/scripts/long_term_forecast/ECL_script/gym/TSGym_False_Stat_MoEMA_False_series-patching_MLP_null_True_HP_48_64-256_2_10_0.0001_null.sh
Generated /data/coding/chaochuan/TSGym/scripts/long_term_forecast/ECL_script/gym/TSGym_False_None_MA_False_series-patching_GRU_null_True_HP_48_64-256_2_20_0.001_type1.sh
Generated /data/coding/chaochuan/TSGym/scripts/long_term_forecast/ECL_script/gym/TSGym_False_DishTS_DFT_True_inverted-encoding_GRU_null_True_HP_192_64-256_3_10_0.0001_null.sh
Generated /data/coding/chaochuan/TSGym/scripts/long_term_forecast/ECL_script/gym/TSGym_False_DishTS_MA_True_series-patching_GRU_null_True_HP_48_256-1024_2_10_0.0001_type1.sh
Generated /data/coding/chaochuan/TSGym/scripts/long_term_forecast/ECL_script/gym/TSGym_False_DishTS_None_True_series-encoding_MLP_null_True_HP_96_64-256_2_20_0.0001_null.sh
Generated /data/coding/chaochuan/TSGym/scripts/long_term_forecast/ECL_script/gym/TSGym_False_Stat_DFT_True_serie